In [215]:
# First we use the pyalgotrading library and the algobull platform to backtest the strategies
from pyalgotrading.algobulls import AlgoBullsConnection
# Import all the strategies from the pyalgotrading library, excluding the option strategies
from aroon_crossover._strategy import AroonCrossover as aroon
from bollinger_bands._strategy import BollingerBands as bollinger
from ema_regular_order._strategy import EMARegularOrder as ema
from inverse_ema_scalping_regular_order._strategy import InverseEMAScalpingRegularOrder as inverse_ema
from macd_crossover._strategy import MACDCrossover as macd
from mean_reversion_bollinger_bands._strategy import MeanReversionBollingerBands as mean_reversion
from reverse_rsi_crossover._strategy import ReverseRSICrossover as reverse_rsi
from rsi_macd_crossover._strategy import RSIMACDCrossover as rsi_macd
from stochastic_crossover._strategy import StochasticCrossover as stochastic
from volatility_trend_atr._strategy import VolatilityTrendATR as volatility_trend
from vwap_crossover._strategy import VWAPCrossover as vwap
strategys = [aroon, bollinger, ema, inverse_ema, macd, mean_reversion, reverse_rsi, rsi_macd, stochastic, volatility_trend, vwap]
strategy_to_name = {
    aroon: "Aroon Crossover",
    bollinger: "Bollinger Bands",
    ema: "EMA Regular Order",
    inverse_ema: "Inverse EMA Scalping Regular Order",
    macd: "MACD Crossover",
    mean_reversion: "Mean Reversion Bollinger Bands",
    reverse_rsi: "Reverse RSI Crossover",
    rsi_macd: "RSI MACD Crossover",
    stochastic: "Stochastic Crossover",
    volatility_trend: "Volatility Trend ATR",
    vwap: "VWAP Crossover"
}
# Establish the connection with the AlgoBulls platform
connection = AlgoBullsConnection()
API_TOKEN = "4fda13e51568abcc27dd18960447c06ea66ff094"
connection.set_access_token(API_TOKEN)

Access token is valid.


In [62]:
# Create the strategies in the AlgoBulls platform and store the strategyIds
strategy_to_id = {}
for strategy in strategys:
    response = connection.create_strategy(strategy, overwrite=True)
    strategy_to_id[strategy] = response['strategyId']


Uploading strategy 'Bollinger Bands' ... Success.
Uploading strategy 'Inverse EMA Scalping Regular Order' ... Success.
Uploading strategy 'MACD Crossover' ... Success.
Uploading strategy 'Mean Reversion Bollinger Bands' ... Success.
Uploading strategy 'Reverse RSI Crossover' ... Success.
Uploading strategy 'RSI MACD Crossover' ... Success.
Uploading strategy 'Stochastic Crossover' ... Success.
Uploading strategy 'Volatility Trend ATR' ... Success.
Uploading strategy 'VWAP Crossover' ... Success.


In [91]:
# Select the instrument
instrument = connection.search_instrument('AAPL', exchange='NASDAQ')[0]['value']
instrument

'NASDAQ:AAPL'

In [92]:
# Create the backtesting parameters
start = '2022-01-01 09:30 -0400'
end = '2024-01-01 15:30 -0400'
lots = 50
capital = 10000

# Strategy parameters
parameters = {
    aroon: {
        'TIME_PERIOD': 12
    },
    bollinger: {
        'STANDARD_DEVIATIONS': 2.0, 
        'TIME_PERIOD': 7.0
    },
    ema: {
        'TIMEPERIOD1': 12, 
        'TIMEPERIOD2': 20
    },
    inverse_ema: {
        'LARGER_TIME_PERIOD': 7.0, 
        'SMALLER_TIME_PERIOD': 2.0
    },
    macd: {
        'TIMEPERIOD_FAST': 12.0, 
        'TIMEPERIOD_SIGNAL': 9.0,
        'TIMEPERIOD_SLOW': 26.0
    },
    mean_reversion: {
        'STD_DEVIATION': 20.0,
        'TIMEPERIOD': 2.0
    },
    reverse_rsi: {
        'OVERBOUGHT_VALUE': 70.0,
        'OVERSOLD_VALUE': 32.0,
        'TIME_PERIOD': 7.0
    },
    rsi_macd: {
        'OVERBOUGHT_VALUE': 85.0,
        'OVERSOLD_VALUE': 15.0,
        'TIMEPERIOD_FAST': 12.0,
        'TIMEPERIOD_RSI': 3.0,
        'TIMEPERIOD_SIGNAL': 9.0,
        'TIMEPERIOD_SLOW': 26.0
    },
    stochastic: {
        'FASTK_PERIOD': 7.0,
        'SLOWD_PERIOD': 2.0,
        'SLOWK_PERIOD': 2.0
    },
    volatility_trend: {
        'ATR_PREV_CANDLES_NUM': 70.0,
        'TIMEPERIOD_ATR': 20.0
    },
    vwap: {
        'TIMEPERIOD': 7.0
    }
}

In [186]:
for strategy, strategyId in strategy_to_id.items():
    connection.backtest(
        strategy=strategyId,
        instrument=instrument,
        start=start,
        end=end,
        lots=lots,
        parameters=parameters[strategy],
        candle='1 hour', # choose a larger interval to reduce the number of candles since the platform is slow
        initial_funds_virtual=capital
    )


Starting the strategy 'VWAP Crossover' in BACKTESTING mode...
╒═════════════════════════╤═══════════════════════════╕
│ Config                  │ Value                     │
╞═════════════════════════╪═══════════════════════════╡
│ Strategy Name           │ VWAP Crossover            │
├─────────────────────────┼───────────────────────────┤
│ Trading Type            │ BACKTESTING               │
├─────────────────────────┼───────────────────────────┤
│ Instrument(s)           │ ['NASDAQ:AAPL']           │
├─────────────────────────┼───────────────────────────┤
│ Quantity/Lots           │ 50                        │
├─────────────────────────┼───────────────────────────┤
│ Start Timestamp         │ 2022-01-01 09:30:00-04:00 │
├─────────────────────────┼───────────────────────────┤
│ End Timestamp           │ 2024-01-01 15:30:00-04:00 │
├─────────────────────────┼───────────────────────────┤
│ Parameters              │ {'TIMEPERIOD': 7.0}       │
├─────────────────────────┼──────────────

In [187]:
# Get backtesting status
for strategy in strategys:
    print(f'The status of the backtesting for the {strategy_to_name[strategy]} strategy is:')
    print(connection.get_backtesting_job_status(strategy_to_id[strategy]))

The status of the backtesting for the Aroon Crossover strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the Bollinger Bands strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the EMA Regular Order strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the Inverse EMA Scalping Regular Order strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the MACD Crossover strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the Mean Reversion Bollinger Bands strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the Reverse RSI Crossover strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the RSI MACD Crossover strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backtesting for the Stochastic Crossover strategy is:
{'message': 'STOPPED', 'status': 0}
The status of the backte

In [188]:
# Get backtesting logs
for strategy in strategys:
    print(f'------------- The log of backtesting {strategy_to_name[strategy]} -----------------')
    logs = connection.get_backtesting_logs(strategy_to_id[strategy])
    print(logs)
    print( '------------- End of log ----------------------------------------')

------------- The log of backtesting VWAP Crossover -----------------
[2024-03-10 10:31:12] Performing sanity checks on cfg strategy_parameters, setting up required data structures...
[2024-03-10 10:31:12] Sanity checks on cfg successful.
[2024-03-10 10:31:12] Currency set to "USD"
[2024-03-10 10:31:12] Setting up broker connection...
[2024-03-10 10:31:15] Starting ALPACAV2 in PAPER mode...
[2024-03-10 10:31:16] Broker connection has been setup successfully.
[2024-03-10 10:31:16] (NASDAQ_EQ) Funds available in client's ABVIRTUALBROKER account is : USD '10000.00'
[2024-03-10 10:31:16] 
########################################
 INITIALIZING ALGOBULLS CORE (v3.3.0)... 
########################################
[2024-03-10 10:31:16] Welcome ALGOBULLS VIRTUAL USER!
[2024-03-10 10:31:16] Reading strategy...
[2024-03-10 10:31:16] Entering Backtesting mode. Henceforth, all timestamps will be Backtesting timestamps...
[BT] [2022-01-01 09:30:00,000] [INFO] [tls] STARTING ALGOBULLS CORE...
[BT] [2

In [117]:
# Stop the backtesting jobs
for strategy in strategys:
    print(f'Stopping the backtesting for the {strategy_to_name[strategy]} strategy')
    connection.stop_backtesting_job(strategy_to_id[strategy])

Stopping the backtesting for the Aroon Crossover strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Bollinger Bands strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the EMA Regular Order strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Inverse EMA Scalping Regular Order strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the MACD Crossover strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Mean Reversion Bollinger Bands strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Reverse RSI Crossover strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the RSI MACD Crossover strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Stochastic Crossover strategy
Stopping BACKTESTING job... Success.
Stopping the backtesting for the Volatility Trend ATR strategy
Stopping BACKTESTING job... Succe

In [217]:
pnl_reports = {}
for strategy in strategys:
    connection.backtesting_pnl_data = None
    print(f'Getting the pnl report for the {strategy_to_name[strategy]} strategy')
    pnl_reports[strategy] = connection.get_backtesting_report_pnl_table(strategy_to_id[strategy])

Getting the pnl report for the Aroon Crossover strategy
Getting the pnl report for the Bollinger Bands strategy
Getting the pnl report for the EMA Regular Order strategy
Getting the pnl report for the Inverse EMA Scalping Regular Order strategy
Getting the pnl report for the MACD Crossover strategy
Getting the pnl report for the Mean Reversion Bollinger Bands strategy
Getting the pnl report for the Reverse RSI Crossover strategy
Getting the pnl report for the RSI MACD Crossover strategy
Getting the pnl report for the Stochastic Crossover strategy
Getting the pnl report for the Volatility Trend ATR strategy
Getting the pnl report for the VWAP Crossover strategy


In [218]:
pnl_reports[aroon]

instrument_segment instrument_tradingsymbol           entry_timestamp  \
0               NASDAQ                     AAPL 2022-01-03 11:30:00-04:00   
1               NASDAQ                     AAPL 2022-01-05 10:30:00-04:00   
2               NASDAQ                     AAPL 2022-01-11 10:30:00-04:00   
3               NASDAQ                     AAPL 2022-01-13 11:30:00-04:00   
4               NASDAQ                     AAPL 2022-01-27 11:30:00-04:00   
5               NASDAQ                     AAPL 2022-02-07 11:30:00-04:00   
6               NASDAQ                     AAPL 2022-02-08 11:30:00-04:00   
7               NASDAQ                     AAPL 2022-02-10 11:30:00-04:00   
8               NASDAQ                     AAPL 2022-02-15 11:30:00-04:00   
9               NASDAQ                     AAPL 2022-02-25 10:30:00-04:00   
10              NASDAQ                     AAPL 2022-03-02 10:30:00-04:00   
11              NASDAQ                     AAPL 2022-03-04 10:30:00-04:00   
12              NASDAQ                     AAPL 2022-03-09 11:30:00-04:00   
13              NASDAQ                     AAPL 2022-03-28 10:30:00-04:00   
14              NASDAQ                     AAPL 2022-03-31 10:30:00-04:00   
15              NASDAQ                     AAPL 2022-04-04 10:30:00-04:00   
16              NASDAQ                     AAPL 2022-04-08 10:30:00-04:00   
17              NASDAQ                     AAPL 2022-04-12 11:30:00-04:00   
18              NASDAQ                     AAPL 2022-04-19 11:30:00-04:00   
19              NASDAQ                     AAPL 2022-04-28 09:30:00-04:00   
20              NASDAQ                     AAPL 2022-05-03 11:30:00-04:00   
21              NASDAQ                     AAPL 2022-05-05 11:30:00-04:00   
22              NASDAQ                     AAPL 2022-05-10 11:30:00-04:00   
23              NASDAQ                     AAPL 2022-05-11 10:30:00-04:00   
24              NASDAQ                     AAPL 2022-05-13 11:30:00-04:00   
25              NASDAQ                     AAPL 2022-05-18 11:30:00-04:00   
26              NASDAQ                     AAPL 2022-05-23 10:30:00-04:00   
27              NASDAQ                     AAPL 2022-05-24 11:30:00-04:00   
28              NASDAQ                     AAPL 2022-05-26 09:30:00-04:00   
29              NASDAQ                     AAPL 2022-05-26 11:30:00-04:00   
30              NASDAQ                     AAPL 2022-06-01 09:30:00-04:00   
31              NASDAQ                     AAPL 2022-06-01 10:30:00-04:00   
32              NASDAQ                     AAPL 2022-06-02 09:30:00-04:00   
33              NASDAQ                     AAPL 2022-06-09 10:30:00-04:00   
34              NASDAQ                     AAPL 2022-06-15 09:30:00-04:00   
35              NASDAQ                     AAPL 2022-06-16 10:30:00-04:00   
36              NASDAQ                     AAPL 2022-06-28 11:30:00-04:00   
37              NASDAQ                     AAPL 2022-07-01 11:30:00-04:00   
38              NASDAQ                     AAPL 2022-07-11 10:30:00-04:00   
39              NASDAQ                     AAPL 2022-07-12 10:30:00-04:00   
40              NASDAQ                     AAPL 2022-07-13 09:30:00-04:00   
41              NASDAQ                     AAPL 2022-07-25 10:30:00-04:00   
42              NASDAQ                     AAPL 2022-07-27 10:30:00-04:00   
43              NASDAQ                     AAPL 2022-08-02 09:30:00-04:00   
44              NASDAQ                     AAPL 2022-08-03 10:30:00-04:00   
45              NASDAQ                     AAPL 2022-08-05 09:30:00-04:00   
46              NASDAQ                     AAPL 2022-08-08 09:30:00-04:00   
47              NASDAQ                     AAPL 2022-08-09 10:30:00-04:00   
48              NASDAQ                     AAPL 2022-08-10 09:30:00-04:00   
49              NASDAQ                     AAPL 2022-08-26 11:30:00-04:00   
50              NASDAQ                     AAPL 2022-09-02 09:30:00-04:00   


In [219]:
# Hide the warnings and erros
import warnings
warnings.filterwarnings('ignore')
statistics = {}
for strategy in strategys[:len(strategys)-1]:
    connection.backtesting_pnl_data = None
    print('-------------------------------------------------------------------')
    print(f'The statistics of backtesting: {strategy_to_name[strategy]}')
    print('-------------------------------------------------------------------')
    statistics[strategy] = connection.get_backtesting_report_statistics(strategy_to_id[strategy])

-------------------------------------------------------------------
The statistics of backtesting: Aroon Crossover
-------------------------------------------------------------------
                    Strategy
------------------  ------------------------
Start Period        2022-01-03
End Period          2023-12-29
Risk-Free Rate      0.0%
Time in Market      100.0%

Cumulative Return   -
CAGR﹪              0.0%

Sharpe              0.36
Prob. Sharpe Ratio  62.0%
Sortino             0.52
Sortino/√2          0.37
Omega               1.07

Max Drawdown        -0.0%
Longest DD Days     353

Gain/Pain Ratio     0.07
Gain/Pain (1M)      0.18

Payoff Ratio        1.02
Profit Factor       -
Common Sense Ratio  1.26
CPC Index           0.56
Tail Ratio          1.0
Outlier Win Ratio   1.0
Outlier Loss Ratio  -

MTD                 1.0000022615023456e+128%
3M                  -
6M                  -
YTD                 -
1Y                  -
3Y (ann.)           0.0%
5Y (ann.)           0.0%
1